# SPICE Running Example for ExoMars2016

This is a Python Jupyter Notebook to illustrate a SPICE running example. 
This could be your very own Python 3 environment, the first thing we will do is indicate that we want the Python package matplotlib to be output in the notebook and to import the SpiceyPy package to use SPICE.

In [2]:
%matplotlib inline

import math
import spiceypy as spiceypy

In [3]:
spiceypy.furnsh('/Users/mcosta/ExoMars2016/kernels/mk/em16_ops_local.tm')

We convert from UTC to Ephemeris Time (ET) to a given SCLK time.

In [16]:
et = spiceypy.utc2et('2018-07-02T11:11:56.208')

id = spiceypy.bodn2c('TGO')
sclk = spiceypy.sce2s(id,et,32)

print(sclk)

1/0072625195:24944


We obtain the NOMAD LNO_OPS_OCC boresight and boresight reference frame

In [17]:
sensor_name = 'TGO_NOMAD_LNO_OPS_NAD'

sensor_id = spiceypy.bodn2c(sensor_name)
(shape, frame, bsight, vectors, bounds) = spiceypy.getfov(sensor_id, 100)

print('{} shape: {}'.format(sensor_name, shape))
print('{} frame: {}'.format(sensor_name, frame))
print('{} bsight: {}'.format(sensor_name, bsight))
print('{} vectors: {}'.format(sensor_name, vectors))
print(bounds)

TGO_NOMAD_LNO_OPS_NAD shape: RECTANGLE
TGO_NOMAD_LNO_OPS_NAD frame: TGO_NOMAD_LNO_OPS_NAD
TGO_NOMAD_LNO_OPS_NAD bsight: [0. 0. 1.]
TGO_NOMAD_LNO_OPS_NAD vectors: 4
[[ 2.18148813e-02  5.81637938e-04  9.99761858e-01]
 [-2.18148813e-02  5.81637938e-04  9.99761858e-01]
 [-2.18148813e-02 -5.81637938e-04  9.99761858e-01]
 [ 2.18148813e-02 -5.81637938e-04  9.99761858e-01]]


We obtain the intersection between the boresight and Mars and we compute the illumination angles

In [36]:
(spoint, trgepc, srfvec ) = spiceypy.sincpt('ELLIPSOID', 'MARS', et, 'IAU_MARS', 'NONE', 'TGO', frame, bsight)

(out, radii) = spiceypy.bodvrd('MARS','RADII', 3)

# Compute flattening coefficient.
re  =  radii[0]
rp  =  radii[2]
f   =  ( re - rp ) / re;

(lon, lat, alt) = spiceypy.recpgr('MARS', spoint, re, f)

lon = spiceypy.dpr()*lon
lat = spiceypy.dpr()*lat

print('TGO_NOMAD_LNO_OPS_NAD boresight intersection with Mars Reference Ellipsoid' + \
      '\n\n LON = {} [deg]\n LAT = {} [deg]\n ALT = {} [km]'.format(lon, lat, alt))

(trgepc, srfvec, phase, solar, emissn) = spiceypy.ilumin('ELLIPSOID', 'MARS', et, 'IAU_MARS', 'NONE', 'TGO', spoint)

print('\n Phase Angle: {} [deg]\n Solar Incidence: {} [deg]'.format(math.degrees(phase), math.degrees(solar)))

TGO_NOMAD_LNO_OPS_NAD boresight intersection with Mars Reference Ellipsoid

 LON = 161.48094104878933 [deg]
 LAT = 52.08143245131205 [deg]
 ALT = -0.0 [km]

 Phase Angle: 112.90362898780457 [deg]
 Solar Incidence: 72.60503765524125 [deg]


We could do the same using a MOLA Low Resolution Digital Shape Kernel
The DSK that we load is as follows:

![title](img/mars_lowres.png)

In [35]:
cspice.furnsh('Users/mcosta/ExoMars2016/kernels/dsk/mars_lowres.bds')

(spoint, trgepc, srfvec ) = spiceypy.sincpt('DSK/UNPRIORITIZED', 'MARS', et, 'IAU_MARS', 'NONE', 'TGO', frame, bsight)

(out, radii) = spiceypy.bodvrd('MARS','RADII', 3)

# Compute flattening coefficient.
re  =  radii[0]
rp  =  radii[2]
f   =  ( re - rp ) / re;

(lon, lat, alt) = spiceypy.recpgr('MARS', spoint, re, f)

lon = spiceypy.dpr()*lon
lat = spiceypy.dpr()*lat

print('TGO_NOMAD_LNO_OPS_NAD boresight intersection with Mars Reference Ellipsoid' + \
      '\n\n LON = {} [deg]\n LAT = {} [deg]\n ALT = {} [km]'.format(lon, lat, alt))

(trgepc, srfvec, phase, solar, emissn) = spiceypy.ilumin('ELLIPSOID', 'MARS', et, 'IAU_MARS', 'NONE', 'TGO', spoint)

print('\n Phase Angle: {} [deg]\n Solar Incidence: {} [deg]'.format(math.degrees(phase), math.degrees(solar)))

Phase Angle: 112.90362898780457 [DEG], Solar Incidence: 72.60503765524125 [DEG]


## spiops a Python Package for OO SPICE and Derived Geometry

Now, we will show the object oriented capabilities of sciops, aimed to easy the way that we interface with SPICE. 
We will define a Time Window, Mars as a target and TGO as an observer:


In [28]:
import spiops as spiops
from spiops.utils import utils

interval = spiops.TimeWindow('2018-07-03T00:00:00', '2018-07-04T00:00:00', resolution=60)

mars = spiops.Target('MARS', time=interval, frame='IAU_MARS')
tgo = spiops.Observer('TGO', time=interval, target=mars)

The spiops library will plot some geometric quantites at our desire

In [29]:
tgo.Plot('distance', notebook=True)

Loading BokehJS ...

So now we have got both data and we can see for instance the MEX-TGO distance for a given time window:

In [33]:
import numpy as np

spiceypy.furnsh('/Users/mcosta/MARS-EXPRESS/kernels/mk/MEX_OPS_LOCAL.TM')

interval = spiops.TimeWindow('2018-07-03T00:00:00', '2018-07-04T00:00:00', resolution=60)

distance = []

timeset = interval.window

for time in timeset:
    state = spiceypy.spkezr('TGO',time,'J2000','NONE','MEX')[0]
    distance.append(np.sqrt(np.power(state[0],2)+np.power(state[1],2)+np.power(state[2],2)))
    
spiops.plot(timeset, [distance],
           yaxis_name=['Distance [km]'],
           title='TGO-MEX Distance', 
           plot_height=500, 
           plot_width=900,
           notebook=True)

Loading BokehJS ...

Now we could provide a Geometry Finder example

In [34]:
import spiceypy.utils.support_types as stypes

MAXIVL = 1000       
MAXWIN = 2 * MAXIVL
TDBFMT = 'YYYY MON DD HR:MN:SC.### (TDB) ::TDB'

# Initialize the "confinement" window with the interval
# over which we'll conduct the search.
cnfine = stypes.SPICEDOUBLE_CELL(2)
spiceypy.wninsd( interval.start, interval.finish, cnfine )
 
#
# In the call below, the maximum number of window
# intervals gfposc can store internally is set to MAXIVL.
# We set the cell size to MAXWIN to achieve this.
#
riswin = stypes.SPICEDOUBLE_CELL( MAXWIN )
 
#
# Now search for the time period, within our confinement
# window, during which the apparent target has elevation
# at least equal to the elevation limit.
#
#  VARIABLE        I/O  DESCRIPTION 
#   --------------- ---  -------------------------------------------------
#   SPICE_GF_CNVTOL  P   Convergence tolerance. 
#   occtyp           I   Type of occultation. 
#   front            I   Name of body occulting the other. 
#   fshape           I   Type of shape model used for front body. 
#   fframe           I   Body-fixed, body-centered frame for front body. 
#   back             I   Name of body occulted by the other. 
#   bshape           I   Type of shape model used for back body. 
#   bframe           I   Body-fixed, body-centered frame for back body. 
#   abcorr           I   Aberration correction flag. 
#   obsrvr           I   Name of the observing body. 
#   step             I   Step size in seconds for finding occultation  
#                        events. 
#   cnfine          I-O  SPICE window to which the search is restricted. 
#  result           O   SPICE window containing results. 
#
spiceypy.gfoclt('ANY','MARS','ELLIPSOID','IAU_MARS','MEX',
                'POINT', '','NONE', 'TGO', 600, cnfine, riswin)
#
# The function wncard returns the number of intervals
# in a SPICE window.
#
winsiz = spiceypy.wncard( riswin )
 
if winsiz == 0:
    print( 'No events were found.' )
 
else:
 
    #
    # Display the visibility time periods.
    #
    print('Occultation times of {0:s} as seen from {1:s}:\n'.format('MMO', 'MPO' ))
 
    for  i  in  range(winsiz):
        #
        # Fetch the start and stop times of
        # the ith interval from the search result
        # window riswin.
        #
        [intbeg, intend] = spiceypy.wnfetd( riswin, i )
 
        #
        # Convert the rise time to a TDB calendar string.
        #
        timstr = spiceypy.timout( intbeg, TDBFMT )
 
        #
        # Write the string to standard output.
        #
        if i==0:
 
            print( 'Occultation start time:'
                '  {:s}'.format( timstr )          )
        else:
 
            print( 'Occultation start time:'
                '  {:s}'.format( timstr )          )
 
        #
        # Convert the set time to a TDB calendar string.
        #
        timstr = spiceypy.timout( intend, TDBFMT )
 
        #
        # Write the string to standard output.
        #
        if  i  ==  (winsiz-1):
 
            print( 'Occultation or window stop time: '
                '  {:s}'.format( timstr )          )
        else:
 
            print( 'Occultation stop time: '
                '  {:s}'.format( timstr )          )
 
        print( ' ' )


Occultation times of MMO as seen from MPO:

Occultation start time:  2018 JUL 03 00:01:09.184 (TDB)
Occultation stop time:   2018 JUL 03 00:24:20.038 (TDB)
 
Occultation start time:  2018 JUL 03 01:10:34.917 (TDB)
Occultation stop time:   2018 JUL 03 01:43:43.450 (TDB)
 
Occultation start time:  2018 JUL 03 02:46:22.152 (TDB)
Occultation stop time:   2018 JUL 03 03:30:02.425 (TDB)
 
Occultation start time:  2018 JUL 03 04:33:48.621 (TDB)
Occultation stop time:   2018 JUL 03 05:24:27.229 (TDB)
 
Occultation start time:  2018 JUL 03 06:12:41.735 (TDB)
Occultation stop time:   2018 JUL 03 06:45:00.591 (TDB)
 
Occultation start time:  2018 JUL 03 07:14:54.317 (TDB)
Occultation stop time:   2018 JUL 03 07:57:30.713 (TDB)
 
Occultation start time:  2018 JUL 03 08:50:11.410 (TDB)
Occultation stop time:   2018 JUL 03 09:27:13.594 (TDB)
 
Occultation start time:  2018 JUL 03 10:32:26.404 (TDB)
Occultation stop time:   2018 JUL 03 11:19:33.827 (TDB)
 
Occultation start time:  2018 JUL 03 12:20:3

Example of how to compute the Schulte Vector

In [12]:
spiceypy.furnsh('/Users/mcosta/BEPICOLOMBO/kernels/ck/bc_mpo_hga_sot_schulte_test_20180317_20500101_f20150124_v01.bc')

obs = 'SCHULTE_ORIGIN'
targ = 'SCHULTE_X_BAND'
ref = 'MPO_SPACECRAFT'

et = spiceypy.utc2et('2027-01-09T20:45:00.000')

schulte, lt = spiceypy.spkpos(targ, et , ref, 'NONE', obs)
schulte, norm = spiceypy.unorm(schulte)

print(schulte)

[ 0.72690173 -0.12305486  0.67562665]
